In [1]:
import numpy as np
import pandas as pd
import json 
import pickle
import torch
import os
from colorama import Style, Fore, Back

import warnings
from sklearn.exceptions import InconsistentVersionWarning
warnings.filterwarnings("ignore", category=InconsistentVersionWarning)
warnings.filterwarnings("ignore", category=UserWarning)

import logging
logger = logging.getLogger(__name__)
logging.basicConfig(
    format=f'{Style.BRIGHT}{Fore.GREEN}%(levelname)s:%(asctime)s{Style.RESET_ALL} {Fore.BLUE}%(message)s{Style.RESET_ALL}', 
    level=logging.INFO
)

In [4]:
from langchain_community.document_loaders  import TextLoader
from langchain_text_splitters import RecursiveCharacterTextSplitter
from langchain_chroma import Chroma 
from langchain_huggingface import HuggingFaceEmbeddings 
from langchain_core.output_parsers import StrOutputParser
from langchain_core.prompts import PromptTemplate
from transformers import pipeline
from langchain_huggingface import HuggingFaceEndpoint
from langchain_core.output_parsers import StrOutputParser

In [6]:
# STEP 1 ~ Document Loader.
loader = TextLoader("5G_logs_v1.txt")
docs = loader.load()
logging.info(f'Size of docx: {len(docs)}')
# logging.info(f'\n{docs[0].page_content}')

# # STEP 2 ~ Split Documents.
text_splitter = RecursiveCharacterTextSplitter(
    chunk_size = 1000, # Each chunk will have 1000 characters
    chunk_overlap = 200, # 200 characters will overlap from consecutive chunks
    add_start_index = True # Output chunks will include a field that specifies the starting pos. in the orig docx.
)
all_splits = text_splitter.split_documents(docs)
logging.info(f'Size of splits: {len(all_splits)}')
logging.info(f'\n{all_splits[0].page_content}')

INFO:2025-01-12 13:40:43,798 Size of docx: 1
INFO:2025-01-12 13:40:43,807 Size of splits: 207
INFO:2025-01-12 13:40:43,808 
Uplink Throughput: 1024 kbps
UE 1 - RACH Process: success
UE 0 - Connection Status: connected
Uplink Throughput: 2048 kbps
UE 1 - Connection Status: disconnected
UE 2 - RACH Process: unsuccessful 
UE 1 - Connection Status: disconnected
UE 1 - Connection Status: disconnected
Downlink Throughput: 1024 kbps
Downlink Throughput: 1024 kbps
Uplink Throughput: 2048 kbps
UE 1 - Connection Status: disconnected
UE 1 - RACH Process: unsuccessful
UE 1 - Connection Status: disconnected
UE 1 - Connection Status: disconnected
UE 1 - Connection Status: disconnected
Downlink Throughput: 1024 kbps
UE 1 - Connection Status: disconnected
UE 0 - Connection Status: connected
Uplink Throughput: 2048 kbps
UE 1 - RACH Process: success
Downlink Throughput: 1024 kbps
UE 2 - RACH Process: unsuccessful 
UE 1 - Connection Status: disconnected
Uplink Throughput: 1024 kbps
UE 1 - Connection Stat

In [13]:
model_embed_name = "sentence-transformers/all-mpnet-base-v2"
model_kwargs = {'device': 'cpu'}
encode_kwargs = {'normalize_embeddings': True}
hf = HuggingFaceEmbeddings(model_name = model_embed_name, \
                           model_kwargs = model_kwargs, \
                           encode_kwargs = encode_kwargs)
vectorstore, vector_db_dir = None, "./5Gdbx"
if os.path.exists(vector_db_dir):
    vectorstore = Chroma(embedding_function = hf, \
                         persist_directory = vector_db_dir)
else:
    logging.warning(f'Creating vector-store from scratch.')
    vectorstore = Chroma.from_documents(documents = all_splits, \
                                        embedding = hf, \
                                        persist_directory = vector_db_dir)
logging.info(vectorstore)

INFO:2025-01-12 14:03:37,737 Load pretrained SentenceTransformer: sentence-transformers/all-mpnet-base-v2
INFO:2025-01-12 14:03:40,097 Anonymized telemetry enabled. See                     https://docs.trychroma.com/telemetry for more information.
INFO:2025-01-12 14:05:19,999 <langchain_chroma.vectorstores.Chroma object at 0x7fc4cc1f6420>


In [14]:
retriever = vectorstore.as_retriever(search_type="similarity", search_kwargs={"k": 1})
retrieved_docs = retriever.invoke("Display all [DEBUG] logs.")
logging.info("\n"+retrieved_docs[0].page_content)

INFO:2025-01-12 14:07:57,794 
UE 0 - Connection Status: connected
UE 2 - RACH Process: unsuccessful 
Uplink Throughput: 1024 kbps
UE 0 - Connection Status: connected
Uplink Throughput: 1024 kbps
Downlink Throughput: 2048 kbps
UE 2 - RACH Process: unsuccessful 
UE 0 - RACH Process: success
UE 2 - RACH Process: unsuccessful 
Uplink Throughput: 1024 kbps
UE 0 - Connection Status: connected
Uplink Throughput: 2048 kbps
UE 0 - Connection Status: connected
Uplink Throughput: 2048 kbps
UE 0 - Connection Status: connected
Uplink Throughput: 1024 kbps
Uplink Throughput: 1024 kbps
UE 1 - RACH Process: success
Uplink Throughput: 2048 kbps
UE 1 - RACH Process: unsuccessful
UE 1 - RACH Process: unsuccessful
Downlink Throughput: 1024 kbps
UE 2 - RACH Process: unsuccessful 
Uplink Throughput: 1024 kbps
UE 1 - RACH Process: unsuccessful
Uplink Throughput: 2048 kbps
UE 1 - Connection Status: disconnected
UE 1 - Connection Status: disconnected
Uplink Throughput: 1024 kbps
UE 0 - Connection Status: conne

In [15]:
template0 = """You are an AI assistant you job is to grade logs into three categories,
BAD, NEUTRAL, GOOD.
LOG --> {log}
GRADE -->"""
prompt = PromptTemplate(input = ["log"], template = template0)

In [16]:
def QA(query):
    # docs = retriever.invoke(query)
    # context = "\n".join(doc.page_content for doc in docs)
    context = query
    return {"log": context}

# model_id = "meta-llama/Llama-3.1-8B-Instruct" -> 16GB model (slow as model cannot be fitted in RAM)
# model_id = "zackli4ai/llama-3.2-1b-instruct-qlora-int4-eo8" -> (4GB but bad results)
# model_id = "meta-llama/Llama-3.2-1B-Instruct" -> (2GB best one)
def llm_resp(response, \
             model_name = "Llama3.2-1B-Instruct/", \
             additional_path = "snapshots/9213176726f574b556790deb65791e0c5aa438b6/"):
    local_dir = "/mnt/d/Desktop/HuggingFaceModels/meta-llama/"
    pipelineX = pipeline("text-generation",
                         model = local_dir + model_name + additional_path,
                         model_kwargs = {"torch_dtype": torch.bfloat16},
                         device_map = "auto",
                         max_length = 128
                        )
    return pipelineX(response.text)[0]['generated_text']

In [39]:
def filter_response(response):
    token = "GRADE: "
    for sentence in response.split("\n"):
        if len(sentence) > len(token) and sentence[:len(token)] == "GRADE: ":
            return sentence[len(token):]
        
def parse_file(rag_chain, filename, cache_name):
    cache = {}
    try:
      with open(f"{cache_name}", "r") as cfile:
          cache = json.load(cfile)
    except: pass
    with open(f"{filename}", "r") as file:
        for sentence in file:
            hash_key = str(hash(sentence))
            is_present = False
            if hash_key in cache: 
              for sentenceX, verdict in cache.get(hash_key):
                  if sentence == sentenceX:
                      is_present = True 
                      break 
            if not is_present:
                verdict = rag_chain.invoke(f"{sentence}")
                if hash_key not in cache: cache[hash_key] = []
                cache[hash_key].append([sentence, verdict])
            logging.info(f"\n{sentence}")
            logging.info(f"\n{filter_response(verdict)}")
            logging.info(f'='*35)
    with open(f"{cache_name}", "w") as cfile:
        json.dump(cache, cfile, indent = 5)
        cache = {} # RESET cache.

## In-house Llama Model.

In [40]:
rag_chain = (
    QA
    | prompt
    | llm_resp
    # | filter_response
)
parse_file(rag_chain, "5G_logs_v1.txt", "cache_autoregressive")

INFO:2025-01-12 15:51:34,607 
Uplink Throughput: 1024 kbps

INFO:2025-01-12 15:51:34,610 
GOOD
INFO:2025-01-12 15:51:34,611 ===================================
INFO:2025-01-12 15:51:34,613 
UE 1 - RACH Process: success



INFO:2025-01-12 15:51:34,614 
GOOD
INFO:2025-01-12 15:51:34,616 ===================================
INFO:2025-01-12 15:51:34,617 
UE 0 - Connection Status: connected

INFO:2025-01-12 15:51:34,618 
GOOD
INFO:2025-01-12 15:51:34,620 ===================================
INFO:2025-01-12 15:51:34,621 
Uplink Throughput: 2048 kbps

INFO:2025-01-12 15:51:34,622 
GOOD
INFO:2025-01-12 15:51:34,623 ===================================
INFO:2025-01-12 15:51:34,625 
UE 1 - Connection Status: disconnected

INFO:2025-01-12 15:51:34,626 
BAD
INFO:2025-01-12 15:51:34,627 ===================================
INFO:2025-01-12 15:51:34,629 
UE 2 - RACH Process: unsuccessful 

INFO:2025-01-12 15:51:34,630 
BAD
INFO:2025-01-12 15:51:34,632 ===================================
INFO:2025-01-12 15:51:34,634 
UE 1 - Connection Status: disconnected

INFO:2025-01-12 15:51:34,635 
BAD
INFO:2025-01-12 15:51:34,636 ===================================
INFO:2025-01-12 15:51:34,637 
UE 1 - Connection Status: disconnected



## Different Models.

In [20]:
def StopHallucinations(response):
    return response.split("\n")[0]

# model_id = "openai-community/gpt2"
model_id = "HuggingFaceH4/zephyr-7b-beta"
llm = HuggingFaceEndpoint(repo_id = model_id, temperature = 0.1)
rag_chain = (
    QA
    | prompt
    | llm
    | StrOutputParser()
    | StopHallucinations
)

parse_file(rag_chain, "5G_logs_v1.txt", "cache_autoreg_online_zephyr")

INFO:2025-01-12 14:12:37,128 
Uplink Throughput: 1024 kbps

INFO:2025-01-12 14:12:37,129 
 GOOD
INFO:2025-01-12 14:12:37,130 ===================================
INFO:2025-01-12 14:12:45,289 
UE 1 - RACH Process: success

INFO:2025-01-12 14:12:45,290 
 GOOD
INFO:2025-01-12 14:12:45,291 ===================================
INFO:2025-01-12 14:12:53,955 
UE 0 - Connection Status: connected

INFO:2025-01-12 14:12:53,957 
 GOOD
INFO:2025-01-12 14:12:53,958 ===================================
INFO:2025-01-12 14:13:01,263 
Uplink Throughput: 2048 kbps

INFO:2025-01-12 14:13:01,264 
 GOOD
INFO:2025-01-12 14:13:01,265 ===================================
INFO:2025-01-12 14:13:08,160 
UE 1 - Connection Status: disconnected

INFO:2025-01-12 14:13:08,161 
 BAD
INFO:2025-01-12 14:13:08,162 ===================================
INFO:2025-01-12 14:13:16,175 
UE 2 - RACH Process: unsuccessful 

INFO:2025-01-12 14:13:16,176 
 BAD
INFO:2025-01-12 14:13:16,177 ===================================
INFO:2025-01-

In [21]:
def StopHallucinations(response):
     return response.split("\n")[0]

model_id = "microsoft/Phi-3.5-mini-instruct"
llm = HuggingFaceEndpoint(repo_id = model_id, temperature = 0.1)
rag_chain = (
    QA
    | prompt
    | llm
    | StrOutputParser()
    | StopHallucinations
)

parse_file(rag_chain, "5G_logs_v1.txt", "cache_autoreg_online_micro")

INFO:2025-01-12 14:16:25,448 
Uplink Throughput: 1024 kbps

INFO:2025-01-12 14:16:25,449 
 NEUTRAL
INFO:2025-01-12 14:16:25,449 ===================================
INFO:2025-01-12 14:16:31,649 
UE 1 - RACH Process: success

INFO:2025-01-12 14:16:31,654 
 GOOD
INFO:2025-01-12 14:16:31,662 ===================================
INFO:2025-01-12 14:16:37,942 
UE 0 - Connection Status: connected

INFO:2025-01-12 14:16:37,951 
 NEUTRAL
INFO:2025-01-12 14:16:37,967 ===================================
INFO:2025-01-12 14:16:44,998 
Uplink Throughput: 2048 kbps

INFO:2025-01-12 14:16:44,999 
 NEUTRAL
INFO:2025-01-12 14:16:45,000 ===================================
INFO:2025-01-12 14:16:51,192 
UE 1 - Connection Status: disconnected

INFO:2025-01-12 14:16:51,193 
 BAD
INFO:2025-01-12 14:16:51,194 ===================================
INFO:2025-01-12 14:16:52,217 
UE 2 - RACH Process: unsuccessful 

INFO:2025-01-12 14:16:52,219 
 BAD
INFO:2025-01-12 14:16:52,220 ===================================
INFO